In [ ]:
import geopandas as gpd
import pandas as pd

# 1. Cargar datos GeoJSON
gdf = gpd.read_file("export.geojson")

# 2. Filtrar solo los restaurantes/cafeterías/bares
gdf = gdf[gdf["amenity"].isin(["restaurant", "cafe", "bar"])]

# 3. Extraer coordenadas (lat, lon)
gdf["lat"] = gdf.geometry.y
gdf["lon"] = gdf.geometry.x

# 4. Estandarizar la categoría de cocina (cuisine)
def normalize_cuisine(value):
    if pd.isna(value):
        return "unknown"
    cuisines = value.lower().replace(" ", "").split(";")
    return cuisines[0]  # Solo la principal

gdf["main_cuisine"] = gdf.get("cuisine", pd.Series(["unknown"] * len(gdf))).apply(normalize_cuisine)

# 5. Crear campos booleanos útiles con lógica más flexible
def has_outdoor(val):
    val = str(val).strip().lower()
    return val in ["yes", "sidewalk", "limited", "maybe"]

def has_wifi(val):
    val = str(val).strip().lower()
    return val in ["yes", "wifi", "wlan"]

def is_wheelchair(val):
    val = str(val).strip().lower()
    return val in ["yes", "designated"]

gdf["has_outdoor_seating"] = gdf["outdoor_seating"].apply(has_outdoor)
gdf["has_wifi"] = gdf["internet_access"].apply(has_wifi)
gdf["is_wheelchair_accessible"] = gdf["wheelchair"].apply(is_wheelchair)

# 6. Limpiar columnas innecesarias y renombrar algunas
columns_to_keep = [
    "name", "amenity", "main_cuisine", "lat", "lon",
    "has_outdoor_seating", "has_wifi", "is_wheelchair_accessible"
]

df_clean = gdf[columns_to_keep].copy()

# 7. Mostrar muestra
print(df_clean.sample(5))

# 8. Guardar CSV o usar para insertarlo en base de datos
df_clean.to_csv("restaurantes_limpios.csv", index=False)


               name     amenity main_cuisine        lat       lon  \
1444        Cazador         bar      unknown  40.424954 -3.706671   
4966           None         bar      unknown  40.475671 -3.714222   
1219        Marotte        cafe  coffee_shop  40.366658 -3.599945   
5436      Boanerges  restaurant       burger  40.381313 -3.646813   
6339  Hijo del Maíz  restaurant      mexican  40.472462 -3.686772   

      has_outdoor_seating  has_wifi  is_wheelchair_accessible  
1444                False     False                     False  
4966                False     False                     False  
1219                False     False                     False  
5436                False     False                     False  
6339                False     False                     False  


In [ ]:
pip install sqlalchemy psycopg2-binary geopandas

In [ ]:
!pip install geopandas folium shapely contextily pyproj -q


In [ ]:
pip install ipywidgets


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 20.7 MB/s eta 0:00:00


In [ ]:
import pandas as pd
import folium
from geopy.distance import geodesic
from folium import Icon
from folium.plugins import MarkerCluster
import ipywidgets as widgets
from IPython.display import display, clear_output

# 1. Cargar los datos
df = pd.read_csv("restaurantes_limpios.csv")
user_location = (40.4168, -3.7038)

# 2. Calcular distancia
df["distance_km"] = df.apply(
    lambda row: geodesic((row["lat"], row["lon"]), user_location).km, axis=1
)

# 3. Filtrar por distancia inicial (dentro de 2km)
df = df[df["distance_km"] <= 2].copy()

# 4. Función para determinar el icono personalizado
def get_icon(row):
    if row["has_outdoor_seating"] and row["has_wifi"]:
        return Icon(color="yellow", icon="info-sign", prefix="fa")
    elif row["has_outdoor_seating"]:
        return Icon(color="green", icon="leaf", prefix="fa")
    elif row["has_wifi"]:
        return Icon(color="blue", icon="wifi", prefix="fa")
    else:
        return Icon(color="gray", icon="ban", prefix="fa")

# 5. Función para generar el mapa con filtros
def generar_mapa(show_wifi, show_terraza):
    clear_output(wait=True)

    # Filtro según checkboxes
    df_filtrado = df[
        (df["has_wifi"] | ~show_wifi) &
        (df["has_outdoor_seating"] | ~show_terraza)
    ]

    # Crear mapa
    m = folium.Map(location=user_location, zoom_start=14)
    folium.Marker(user_location, tooltip="Tú estás aquí", icon=folium.Icon(color="red")).add_to(m)

    # Agrupador de marcadores
    marker_cluster = MarkerCluster().add_to(m)

    for _, row in df_filtrado.iterrows():
        popup_info = f"""
        <b>{row['name']}</b><br>
        Cocina: {row['main_cuisine']}<br>
        Terraza: {"✅" if row["has_outdoor_seating"] else "❌"}<br>
        WiFi: {"✅" if row["has_wifi"] else "❌"}<br>
        Accesible: {"✅" if row.get("is_wheelchair_accessible", False) else "❌"}<br>
        Distancia: {row['distance_km']:.2f} km
        """
        folium.Marker(
            location=[row["lat"], row["lon"]],
            tooltip=row["name"],
            popup=folium.Popup(popup_info, max_width=300),
            icon=get_icon(row)
        ).add_to(marker_cluster)

    # Mostrar mapa
    display(m)

# 6. Widgets de filtro
wifi_checkbox = widgets.Checkbox(value=False, description="Con WiFi")
terraza_checkbox = widgets.Checkbox(value=False, description="Con Terraza")

ui = widgets.HBox([wifi_checkbox, terraza_checkbox])

def on_change(change):
    generar_mapa(wifi_checkbox.value, terraza_checkbox.value)

wifi_checkbox.observe(on_change, names='value')
terraza_checkbox.observe(on_change, names='value')

# Mostrar widgets y mapa inicial
display(ui)
generar_mapa(wifi_checkbox.value, terraza_checkbox.value)


<ipython-input-24-5d03fb8b7003>:24: UserWarning: color argument of Icon should be one of: {'purple', 'pink', 'lightblue', 'orange', 'green', 'darkblue', 'darkpurple', 'blue', 'lightgray', 'cadetblue', 'red', 'lightgreen', 'beige', 'gray', 'darkred', 'black', 'lightred', 'white', 'darkgreen'}.
  return Icon(color="yellow", icon="info-sign", prefix="fa")


In [ ]:
import pandas as pd
from geopy.distance import geodesic
import folium
from folium import Icon
from folium.plugins import MarkerCluster

# Cargar los datos
df = pd.read_csv("restaurantes_limpios.csv")
user_location = (40.4168, -3.7038)
df["distance_km"] = df.apply(lambda row: geodesic((row["lat"], row["lon"]), user_location).km, axis=1)

# Parámetros de filtrado (ajusta manualmente aquí)
filtro_wifi = False
filtro_terraza = True

# Aplicar filtros
df_filtrado = df.copy()
if filtro_wifi:
    df_filtrado = df_filtrado[df_filtrado["has_wifi"] == True]
if filtro_terraza:
    df_filtrado = df_filtrado[df_filtrado["has_outdoor_seating"] == True]

# Crear el mapa
m = folium.Map(location=user_location, zoom_start=14)
folium.Marker(user_location, tooltip="Tú estás aquí", icon=folium.Icon(color="red")).add_to(m)
cluster = MarkerCluster().add_to(m)

def get_icon(row):
    if row["has_outdoor_seating"] and row["has_wifi"]:
        return Icon(color="yellow", icon="info-sign", prefix="fa")
    elif row["has_outdoor_seating"]:
        return Icon(color="green", icon="leaf", prefix="fa")
    elif row["has_wifi"]:
        return Icon(color="blue", icon="wifi", prefix="fa")
    else:
        return Icon(color="gray", icon="ban", prefix="fa")

# Añadir marcadores
for _, row in df_filtrado.iterrows():
    popup_info = f"""
    <b>{row['name']}</b><br>
    Cocina: {row['main_cuisine']}<br>
    Terraza: {"✅" if row["has_outdoor_seating"] else "❌"}<br>
    WiFi: {"✅" if row["has_wifi"] else "❌"}<br>
    Distancia: {row['distance_km']:.2f} km
    """
    folium.Marker(
        location=[row["lat"], row["lon"]],
        popup=popup_info,
        icon=get_icon(row)
    ).add_to(cluster)

# Mostrar mapa
m


<ipython-input-27-0cac4c0a3f9a>:30: UserWarning: color argument of Icon should be one of: {'purple', 'pink', 'lightblue', 'orange', 'green', 'darkblue', 'darkpurple', 'blue', 'lightgray', 'cadetblue', 'red', 'lightgreen', 'beige', 'gray', 'darkred', 'black', 'lightred', 'white', 'darkgreen'}.
  return Icon(color="yellow", icon="info-sign", prefix="fa")


In [ ]:
!pip install geopy -q


In [ ]:
from geopy.distance import geodesic
import pandas as pd

# Cargar datos
df = pd.read_csv("restaurantes_limpios.csv")

# Coordenadas del usuario (puedes cambiarlas)
user_location = (40.416729, -3.703339)  # Puerta del sol

# Calcular la distancia entre el usuario y cada restaurante
df["distance_km"] = df.apply(lambda row: geodesic(user_location, (row["lat"], row["lon"])).km, axis=1)

# Filtros: distancia y atributos (ajusta según quieras)
df_filtrado = df[
    (df["distance_km"] <= 10) &
    ((df["has_outdoor_seating"] == True) | (df["has_wifi"] == True))
]


# Resultado
print(f"Restaurantes filtrados: {len(df_filtrado)}")
df_filtrado.head()


Restaurantes filtrados: 407


name     amenity main_cuisine        lat       lon  \
0                   NaN        cafe      unknown  40.478705 -3.711481   
6   La Parrilla de Nino  restaurant      unknown  40.425766 -3.712090   
7             Taj Mahal  restaurant       indian  40.425140 -3.711853   
17            Tío Timón  restaurant     regional  40.413159 -3.711747   
25           Casa Mingo  restaurant      chicken  40.424971 -3.725254   

    has_outdoor_seating  has_wifi  is_wheelchair_accessible  distance_km  
0                  True     False                     False     6.916584  
6                  True     False                     False     1.248376  
7                  True     False                     False     1.180868  
17                 True     False                     False     0.816318  
25                 True     False                     False     2.072869

In [ ]:
m.save("restaurantes_madrid.html")


In [ ]:
# Comprobar el restaurante en los datos originales y los datos limpios
restaurante_nombre = "La Rollerie"
print("Datos Originales:")
print(gdf[gdf["name"] == restaurante_nombre][["name", "amenity", "cuisine", "outdoor_seating", "internet_access", "wheelchair"]])

print("\nDatos Limpios:")
print(df_clean[df_clean["name"] == restaurante_nombre][["name", "main_cuisine", "has_outdoor_seating", "has_wifi", "is_wheelchair_accessible"]])


Datos Originales:
             name     amenity      cuisine outdoor_seating internet_access  \
399   La Rollerie        cafe  coffee_shop            None            wlan   
1191  La Rollerie  restaurant         None            None            None   
2590  La Rollerie        cafe         None             yes            None   
4628  La Rollerie        cafe         None            None            None   
6106  La Rollerie  restaurant         None            None            None   

     wheelchair  
399          no  
1191       None  
2590       None  
4628         no  
6106       None  

Datos Limpios:
             name main_cuisine  has_outdoor_seating  has_wifi  \
399   La Rollerie  coffee_shop                False      True   
1191  La Rollerie      unknown                False     False   
2590  La Rollerie      unknown                 True     False   
4628  La Rollerie      unknown                False     False   
6106  La Rollerie      unknown                False     False   

In [ ]:
# Verificar la lógica de clasificación
def clasificar_icono(row):
    terraza = row["has_outdoor_seating"]
    wifi = row["has_wifi"]

    if terraza and wifi:
        return "amarillo"
    elif terraza:
        return "verde"
    elif wifi:
        return "azul"
    else:
        return "gris"

df_filtrado["tipo_icono"] = df_filtrado.apply(clasificar_icono, axis=1)

# Mostrar una tabla con los datos relevantes
columnas_a_mostrar = [
    "name", "main_cuisine", "has_outdoor_seating", "has_wifi", "distance_km", "tipo_icono"
]

# Mostrar primeros 15 resultados
df_filtrado[columnas_a_mostrar].sort_values("distance_km").head(15)


name   main_cuisine  has_outdoor_seating  has_wifi  \
4396  Puerta al sol by Chicote        unknown                False     False   
4776               Cafe Europa        spanish                False     False   
4775                  De Maria        spanish                False     False   
4222                Casa Labra        unknown                False     False   
2464             All U Can Eat        spanish                False     False   
4674         Cafetería Armenia        unknown                False     False   
5991      La Arepera Resto-bar          arepa                False     False   
3480                      Vips  international                False     False   
2987                   Wowble!          asian                False     False   
2723                 Starbucks    coffee_shop                False     False   
3074                   Wok Sun          asian                False     False   
4673                 Café & Té        unknown                False     False   
2722             Cañas y Tapas        unknown                False     False   
3261                  Serafina        unknown                False     False   
3755      Rosi La Loca Taberna        unknown                False     False   

      distance_km tipo_icono  
4396     0.051366       gris  
4776     0.068278       gris  
4775     0.071162       gris  
4222     0.079359       gris  
2464     0.097921       gris  
4674     0.099398       gris  
5991     0.104648       gris  
3480     0.111712       gris  
2987     0.112020       gris  
2723     0.119304       gris  
3074     0.120937       gris  
4673     0.121048       gris  
2722     0.129087       gris  
3261     0.131222       gris  
3755     0.131409       gris

In [ ]:
# Ver cuántos valores había originalmente antes de normalizar
print("Valores únicos en 'outdoor_seating':")
print(gdf["outdoor_seating"].value_counts(dropna=False))

print("\nValores únicos en 'internet_access':")
print(gdf["internet_access"].value_counts(dropna=False))


Valores únicos en 'outdoor_seating':
outdoor_seating
None        6673
yes          423
no           196
sidewalk       1
Name: count, dtype: int64

Valores únicos en 'internet_access':
internet_access
None    7162
wlan     103
yes       16
no        12
Name: count, dtype: int64


In [ ]:
print("\nHas outdoor seating:")
print(df_clean["has_outdoor_seating"].value_counts())

print("\nHas wifi:")
print(df_clean["has_wifi"].value_counts())



Has outdoor seating:
has_outdoor_seating
False    6869
True      424
Name: count, dtype: int64

Has wifi:
has_wifi
False    7174
True      119
Name: count, dtype: int64
